In [1]:
# from selenium import webdriver
# from selenium.webdriver.common.by import By
# from selenium.webdriver.common.keys import Keys
# from bs4 import BeautifulSoup
# import time
# # !pip install tensorflow tensorflow-hub
# import tensorflow as tf
# import tensorflow_hub as hub
# import numpy as np
# # !pip install jellyfish
# import jellyfish

In [2]:
# !pip show selenium
# !pip show beautifulsoup4
# !pip show numpy
# !pip show tensorflow
# !pip show tensorflow-hub
# !pip show jellyfish
# !pip show streamlit

In [3]:
# starting_topic = "soulja boy"
# target_topic = "fart"

# play_wiki_game(starting_topic = starting_topic, target_topic = target_topic, limit = 50)

# Version 3

In [4]:
from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.common.keys import Keys
from bs4 import BeautifulSoup
import time
# !pip install tensorflow tensorflow-hub
import tensorflow as tf
import tensorflow_hub as hub
import numpy as np
import requests
import json

# Load the pre-trained Universal Sentence Encoder
embed = hub.load("https://tfhub.dev/google/universal-sentence-encoder/4")

2023-07-30 09:07:17.451238: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [105]:
def most_similar_sentence(target_topic, labels_list):
    # Encode the context sentence and all sentences in the list
    context_embedding = embed([target_topic])[0]
    sentence_embeddings = embed(labels_list)
    
    # Calculate cosine similarities between the context sentence and each sentence in the list
    similarities = np.inner(context_embedding, sentence_embeddings)
    
    # Find the index of the most similar sentence
    most_similar_index = np.argmax(similarities)
    
    return labels_list[most_similar_index], similarities[most_similar_index], most_similar_index

def search_wikipedia(search_term):
    # Define the endpoint
    endpoint = "https://en.wikipedia.org/w/api.php"

    # Define the search parameters
    params = {
        "action": "query",
        "format": "json",
        "list": "search",
        "srsearch": search_term
    }

    # Send a GET request to the endpoint with your parameters
    response = requests.get(url = endpoint, params = params)

    # Parse the results as JSON
    data = json.loads(response.text)

    # Get the title of the first result (this will be used as the page title in the next step)
    page_title = data["query"]["search"][0]["title"]

    # if "may refer to" in data["query"]["search"][0]["snippet"].lower():
    #     page_title = data["query"]["search"][1]["title"]

    # Construct the URL of the Wikipedia page
    page_url = "https://en.wikipedia.org/wiki/{}".format(page_title.replace(" ", "_"))

    return page_url, page_title

def get_topic_context(driver, more = False):
    # Find the first paragraph of the main article
    first_paragraph = driver.find_element(By.CSS_SELECTOR, "div.mw-parser-output > p:not(.mw-empty-elt)").text

    if more:
        context_sentence = ". ".join(first_paragraph.split(". ")[:5])
    else:
        context_sentence = first_paragraph.split(". ")[0]

    return context_sentence

# bad_words = [word for word in open("censored.txt", "r").readlines()]
bad_words = [word.strip() for word in open("censored.txt", "r").readlines()]

def refine_links(topic, links, current_url_suffix, used_links, used_topics, censor = False):

    links_texts = []

    # Iterate through the links and extract their URLs
    for link in links:
        link_url = link.get('href')
        if link_url and link_url.startswith("/wiki/"):
            link_url = "https://en.wikipedia.org" + link_url
            link_text = link.text.strip() # Get the text and remove leading/trailing spaces

            # make sure they are both not None
            if link_text and current_url_suffix not in link_url:

                if link_url not in used_links and link_text.lower() not in [topic.lower() for topic in used_topics]:

                    # eliminates topic duplicates, non-wiki links, and wiki-help pages (non-content pages)
                    if topic.lower() not in link_url.lower() and "en.wikipedia.org/wiki/" in link_url and ":" not in "".join(link_url.split("/")[1:]) and "Main_Page" != str(link_url.split("/")[-1]):

                        # censoring if needed
                        if censor:
                            if not any(word1.lower() in bad_words for word1 in [word.lower() for word in link_text.split()]):
                                links_texts.append((link_url, link_text))
                        else:
                            links_texts.append((link_url, link_text))

    return links_texts

def play_wiki_game(starting_topic: str, target_topic: str, limit: int = 100):

    ##### Setup Chrome options
    chrome_options = webdriver.ChromeOptions()
    chrome_options.add_argument("--headless")  # Ensure GUI is off
    chrome_options.add_argument("--no-sandbox")
    chrome_options.add_argument("--disable-dev-shm-usage")
    driver = webdriver.Chrome(options = chrome_options)

    #### Getting target url, topic, and context
    driver_target = webdriver.Chrome(options = chrome_options)
    target_url, target_topic = search_wikipedia(search_term = target_topic)
    driver_target.get(target_url)
    target_context = get_topic_context(driver_target, more = True)
    # print(target_context)
    driver_target.quit()

    topic = starting_topic
    num_pages = 0
    used_topics = []
    used_links = []

    start_time = time.time()

    ### BEGIN ###

    print("-" * 150)
    print(f"\nStarting!\n")
    print("-" * 150)

    url, topic = search_wikipedia(search_term = starting_topic)
    driver.get(url)
    used_topics.append(topic)
    used_links.append(driver.current_url)

    while True:
        # increment the page tracking by 1 for each new page
        num_pages += 1

        # if not the first page, navigate to the new page
        if num_pages > 1:
            driver.get(next_link)

        try:
            context_sentence = get_topic_context(driver)
        except Exception as e:
            context_sentence = "Context could not be found from webpage"

        current_url = driver.current_url
        current_url_suffix = str(current_url).split("/")[-1]

        ### Use BeautifulSoup and Requests instead of Selenium for link extraction
        current_page = driver.page_source # html from Selenium instead of BeautifulSoup

        soup = BeautifulSoup(current_page, 'html.parser')

        links = soup.find_all('a')

        # get rid of any bloat in the links from the page
        links_texts = refine_links(topic, links, current_url_suffix, used_links, used_topics)

        # best_label, best_score, loc_idx = most_similar_sentence(target_topic = target_topic, labels_list = [text for link, text in links_texts])
        best_label, best_score, loc_idx = most_similar_sentence(target_topic = target_context.lower(), labels_list = [text.lower() for link, text in links_texts])

        print(f"\nPage: {num_pages}")
        print(f"Current topic: '{topic.title()}'")
        print(f"Current URL: '{current_url}'")
        print(f"Current Topic Context: '{context_sentence}'")
        if current_url != target_url:
            print(f"Next topic: '{best_label.title()}'. Semantic similarity to '{target_topic.title()}': {round((best_score * 100), 2)}%")

        next_link, topic = links_texts[loc_idx]

        used_links.append(next_link)
        used_topics.append(topic)

        if current_url == target_url: # because the target_url is now found through the API
            print("\n" + "-" * 150)
            print(f"\nFrom '{starting_topic.title()}', to '{target_topic.title()}' in {num_pages} pages, {round(time.time() - start_time, 2)} seconds!")
            print(f"Starting topic: '{starting_topic.title()}': '{used_links[0]}'")
            print(f"Target topic: '{target_topic.title()}': '{target_url}'\n")
            print("-" * 150)
            driver.quit()
            break

        if num_pages == limit:
            print("\n" + "-" * 150)
            print(f"\nUnfortunately, the model couldn't get from '{starting_topic.title()}', to '{target_topic.title()}' in {num_pages} pages or less.")
            print(f"In {round(time.time() - start_time, 2)} seconds, it got from '{starting_topic.title()}': '{used_links[0]}', to '{used_topics[-1].title()}': '{used_links[-1]}'")
            print(f"\nTry a different combination to see if it can do it!\n")
            print("-" * 150)
            driver.quit()
            break

###### Example

starting_topic = 'soulja boy'
target_topic = 'urine'

play_wiki_game(starting_topic = starting_topic, target_topic = target_topic, limit = 50)

------------------------------------------------------------------------------------------------------------------------------------------------------

Starting!

------------------------------------------------------------------------------------------------------------------------------------------------------

Page: 1
Current topic: 'Soulja Boy'
Current URL: 'https://en.wikipedia.org/wiki/Soulja_Boy'
Current Topic Context: 'DeAndre Cortez Way (born July 28, 1990), known professionally as Soulja Boy (formerly Soulja Boy Tell 'Em), is an American rapper and record producer'
Next topic: 'Peewee Longway'. Semantic similarity to 'Urine': 21.81%

Page: 2
Current topic: 'Peewee Longway'
Current URL: 'https://en.wikipedia.org/wiki/Peewee_Longway'
Current Topic Context: 'Quincy Lamont Williams (born August 17, 1984), known by his stage name Peewee Longway, is an American rapper best known for his mixtape The Blue M&M and his collaboration with Young Thug, "Loaded"'
Next topic: 'Hip Hop'. Sem

In [6]:
# starting_topic = 'soulja boy'
# target_topic = 'fart'

# play_wiki_game(starting_topic = starting_topic, target_topic = target_topic, limit = 50)

# Tracking Stats

In [73]:
def play_wiki_game_stats(starting_topic: str, target_topic: str, limit: int = 200):

    stats_dict = {}

    ##### Setup Chrome options
    chrome_options = webdriver.ChromeOptions()
    chrome_options.add_argument("--headless")  # Ensure GUI is off
    chrome_options.add_argument("--no-sandbox")
    chrome_options.add_argument("--disable-dev-shm-usage")
    driver = webdriver.Chrome(options = chrome_options)

    #### Getting target url, topic, and context
    driver_target = webdriver.Chrome(options = chrome_options)
    target_url, target_topic = search_wikipedia(search_term = target_topic)
    driver_target.get(target_url)
    target_context = get_topic_context(driver_target)
    print(target_context)
    print()
    driver_target.quit()
    
    topic = starting_topic
    num_pages = 0
    used_topics = []
    used_links = []
    contexts = []
    sim_to_target_scores = []

    start_time = time.time()

    ### BEGIN ###

    print("-" * 150)
    print(f"\nStarting!\n")
    print("-" * 150)

    url, topic = search_wikipedia(search_term = starting_topic)
    driver.get(url)
    used_topics.append(topic)
    used_links.append(driver.current_url)
    sim_to_target_scores.append(most_similar_sentence(target_topic = target_context, labels_list = [topic])[1])

    while True:
        # increment the page tracking by 1 for each new page
        num_pages += 1

        # if not the first page, navigate to the new page
        if num_pages > 1:
            driver.get(next_link)

        context_sentence = get_topic_context(driver)
        contexts.append(context_sentence)

        current_url = driver.current_url
        current_url_suffix = str(current_url).split("/")[-1]

        ### Use BeautifulSoup and Requests instead of Selenium for link extraction
        current_page = driver.page_source # html from Selenium instead of BeautifulSoup

        soup = BeautifulSoup(current_page, 'html.parser')

        links = soup.find_all('a')

        # get rid of any bloat in the links from the page
        links_texts = refine_links(topic, links, current_url_suffix, used_links, used_topics)

        best_label, best_score, loc_idx = most_similar_sentence(target_topic = target_context, labels_list = [text for link, text in links_texts])

        print(f"\nPage: {num_pages}")
        print(f"Current topic: '{topic.title()}'")
        print(f"Current URL: '{current_url}'")
        print(f"Current Topic Context: '{context_sentence}'")
        if current_url != target_url:
            print(f"Next topic: '{best_label.title()}'. Semantic similarity to '{target_topic.title()}': {round((best_score * 100), 2)}%")
        
        next_link, topic = links_texts[loc_idx]

        # contexts.append(context_sentence)

        if current_url == target_url: # because the target_url is now found through the API
            print("\n" + "-" * 150)
            print(f"\nFrom '{starting_topic.title()}', to '{target_topic.title()}' in {num_pages} pages, {round(time.time() - start_time, 2)} seconds!")
            print(f"Starting topic: '{starting_topic.title()}': '{used_links[0]}'")
            print(f"Target topic: '{target_topic.title()}': '{used_links[-1]}'\n")
            print("-" * 150)

            stats_dict['start_end'] = [f"{starting_topic}_{target_topic}" for i in range(num_pages)]
            stats_dict['topic'] = used_topics
            stats_dict['context'] = contexts
            stats_dict['sim_to_target'] = sim_to_target_scores
            stats_dict['url'] = used_links
            stats_dict['page_num'] = [i+1 for i in range(num_pages)]
            driver.quit()
            return stats_dict
            break

        ##### ADD DRAMATIC DELAY HERE #####
        # time.sleep(0.5)
        # time.sleep(10)

        if num_pages == limit:
            print("\n" + "-" * 150)
            print(f"\nUnfortunately, the model couldn't get from '{starting_topic.title()}', to '{target_topic.title()}' in {num_pages} pages or less.")
            print(f"In {round(time.time() - start_time, 2)} seconds, it got from '{starting_topic.title()}': '{used_links[0]}', to '{used_topics[-1].title()}': '{used_links[-1]}'")
            print(f"\nTry a different combination to see if it can do it!\n")
            print("-" * 150)

            stats_dict['start_end'] = [f"{starting_topic}_{target_topic}" for i in range(num_pages)]
            stats_dict['topic'] = used_topics
            stats_dict['context'] = contexts
            stats_dict['sim_to_target'] = sim_to_target_scores
            stats_dict['url'] = used_links
            stats_dict['page_num'] = [i+1 for i in range(num_pages)]
            driver.quit()
            return stats_dict
            break

        used_links.append(next_link)
        used_topics.append(topic)
        sim_to_target_scores.append(best_score)

# starting_topic = 'john mayer'
# target_topic = 'fart'

# stats_dict = play_wiki_game_stats(starting_topic = starting_topic, target_topic = target_topic, limit = 200)

In [35]:
# stats_dict['start_end'] = [f"{starting_topic}_{target_topic}" for i in range(7)]
print(stats_dict.keys())
print([len(stats_dict[key]) for key in stats_dict.keys()])

dict_keys(['start_end', 'topic', 'context', 'sim_to_target', 'url', 'page_num'])
[6, 6, 6, 6, 6, 6]


In [36]:
stats_dict['sim_to_target']

[0.027460583, 0.20852715, 0.2775123, 0.31147623, 0.4413054, 0.6199604]

In [37]:
import pandas as pd
stats_df = pd.DataFrame(stats_dict)
stats_df

start_end                          topic  \
0  john mayer_Flatulence                     John Mayer   
1  john mayer_Flatulence            cardiac dysrhythmia   
2  john mayer_Flatulence                       prolapse   
3  john mayer_Flatulence  gastrointestinal disturbances   
4  john mayer_Flatulence         gastrointestinal tract   
5  john mayer_Flatulence                     flatulence   

                                             context  sim_to_target  \
0  John Clayton Mayer[1] (/ˈmeɪ.ər/ MAY-ər; born ...       0.027461   
1  Arrhythmias, also known as cardiac arrhythmias...       0.208527   
2  Mitral valve prolapse (MVP) is a valvular hear...       0.277512   
3                  Gastrointestinal diseases (abbrev       0.311476   
4  The gastrointestinal tract (GI tract, digestiv...       0.441305   
5  Flatulence, in humans, is the expulsion of gas...       0.619960   

                                                 url  page_num  
0           https://en.wikipedia.org/wiki/John_Mayer         1  
1  https://en.wikipedia.org/wiki/Cardiac_dysrhythmia         2  
2  https://en.wikipedia.org/wiki/Mitral_valve_pro...         3  
3  https://en.wikipedia.org/wiki/Gastrointestinal...         4  
4  https://en.wikipedia.org/wiki/Human_gastrointe...         5  
5           https://en.wikipedia.org/wiki/Flatulence         6

# Simluations

In [42]:
import itertools

unrelated_list = [
    "Sushi",
    "Mars",
    "Beethoven",
    "Mount Everest",
    "Humpback Whale",
    "The Great Wall of China",
    "Photography",
    "Pyramids of Egypt",
    "Albert Einstein",
    "Rainforests",
    'buggy'
]

# Generate all permutations of pairs
pair_permutations = list(itertools.permutations(unrelated_list, 2))

print(len(pair_permutations)) # no pairs with self
pair_permutations[:5]

110


[('Sushi', 'Mars'),
 ('Sushi', 'Beethoven'),
 ('Sushi', 'Mount Everest'),
 ('Sushi', 'Humpback Whale'),
 ('Sushi', 'The Great Wall of China')]

In [43]:
# Initial dictionary
main_dict = {
    'fruits': ['apple', 'banana', 'orange'],
    'animals': ['cat', 'dog', 'elephant'],
}

# Function to add a new dictionary to the main_dict
def add_to_main_dict(main_dict, new_dict):
    for key, value in new_dict.items():
        if key in main_dict:
            main_dict[key].extend(value)
        else:
            main_dict[key] = value

# New dictionary to add to main_dict
new_dict1 = {
    'fruits': ['grapes', 'kiwi'],
    'cities': ['New York', 'London'],
}

# Add new_dict1 to main_dict
add_to_main_dict(main_dict, new_dict1)

# New dictionary to add to main_dict
new_dict2 = {
    'animals': ['tiger', 'lion'],
    'colors': ['red', 'blue'],
}

# Add new_dict2 to main_dict
add_to_main_dict(main_dict, new_dict2)

# Print the updated main_dict
print(main_dict)


{'fruits': ['apple', 'banana', 'orange', 'grapes', 'kiwi'], 'animals': ['cat', 'dog', 'elephant', 'tiger', 'lion'], 'cities': ['New York', 'London'], 'colors': ['red', 'blue']}


In [63]:
def play_wiki_game_stats(starting_topic: str, target_topic: str, limit: int = 200):

    stats_dict = {}

    ##### Setup Chrome options
    chrome_options = webdriver.ChromeOptions()
    chrome_options.add_argument("--headless")  # Ensure GUI is off
    chrome_options.add_argument("--no-sandbox")
    chrome_options.add_argument("--disable-dev-shm-usage")
    driver = webdriver.Chrome(options = chrome_options)

    #### Getting target url, topic, and context
    driver_target = webdriver.Chrome(options = chrome_options)
    target_url, target_topic = search_wikipedia(search_term = target_topic)
    driver_target.get(target_url)
    target_context = get_topic_context(driver_target)
    driver_target.quit()
    
    topic = starting_topic
    num_pages = 0
    used_topics = []
    used_links = []
    contexts = []
    sim_to_target_scores = []

    start_time = time.time()

    url, topic = search_wikipedia(search_term = starting_topic)
    driver.get(url)
    used_topics.append(topic)
    used_links.append(driver.current_url)
    sim_to_target_scores.append(most_similar_sentence(target_topic = target_context, labels_list = [topic])[1])

    while True:
        # increment the page tracking by 1 for each new page
        num_pages += 1

        # if not the first page, navigate to the new page
        if num_pages > 1:
            driver.get(next_link)

        context_sentence = get_topic_context(driver)
        contexts.append(context_sentence)

        current_url = driver.current_url
        current_url_suffix = str(current_url).split("/")[-1]

        ### Use BeautifulSoup and Requests instead of Selenium for link extraction
        current_page = driver.page_source # html from Selenium instead of BeautifulSoup

        soup = BeautifulSoup(current_page, 'html.parser')

        links = soup.find_all('a')

        # get rid of any bloat in the links from the page
        links_texts = refine_links(topic, links, current_url_suffix, used_links, used_topics)

        best_label, best_score, loc_idx = most_similar_sentence(target_topic = target_context, labels_list = [text for link, text in links_texts])

        print(f"Start: '{starting_topic}'. End: '{target_topic}'. Page: {num_pages}", end = '\r')

        next_link, topic = links_texts[loc_idx]

        if current_url == target_url: # because the target_url is now found through the API
            print()
            stats_dict['start'] = [starting_topic for i in range(num_pages)]
            stats_dict['target'] = [target_topic for i in range(num_pages)]
            stats_dict['topic'] = used_topics
            stats_dict['context'] = contexts
            stats_dict['sim_to_target'] = sim_to_target_scores
            # stats_dict['time_seconds'] = times
            stats_dict['url'] = used_links
            stats_dict['page_num'] = [i+1 for i in range(num_pages)]
            add_to_main_dict(master_dict, stats_dict)
            driver.quit()
            break

        if num_pages == limit:
            print()
            stats_dict['start'] = [starting_topic for i in range(num_pages)]
            stats_dict['target'] = [target_topic for i in range(num_pages)]
            stats_dict['topic'] = used_topics
            stats_dict['context'] = contexts
            stats_dict['sim_to_target'] = sim_to_target_scores
            stats_dict['url'] = used_links
            stats_dict['page_num'] = [i+1 for i in range(num_pages)]
            driver.quit()
            add_to_main_dict(master_dict, stats_dict)
            break

        used_links.append(next_link)
        used_topics.append(topic)
        sim_to_target_scores.append(best_score)

master_dict = {}
master_dict['start'] = []
master_dict['target'] = []
master_dict['topic'] = []
master_dict['context'] = []
master_dict['sim_to_target'] = []
master_dict['url'] = []
master_dict['page_num'] = []

# starting_topic = 'john mayer'
# target_topic = 'fart'

for starting_topic, target_topic in pair_permutations:
    play_wiki_game_stats(starting_topic = starting_topic, target_topic = target_topic, limit = 200)

Start: 'Sushi'. End: 'Mars'. Page: 8
Start: 'Sushi'. End: 'Ludwig van Beethoven'. Page: 9
Start: 'Sushi'. End: 'Mount Everest'. Page: 4
Start: 'Sushi'. End: 'Humpback whale'. Page: 3
Start: 'Sushi'. End: 'Great Wall of China'. Page: 7
Start: 'Sushi'. End: 'Photography'. Page: 29
Start: 'Sushi'. End: 'Egyptian pyramids'. Page: 23
Start: 'Sushi'. End: 'Albert Einstein'. Page: 12
Start: 'Sushi'. End: 'Rainforest'. Page: 7
Start: 'Sushi'. End: 'Buggy'. Page: 200
Start: 'Mars'. End: 'Sushi'. Page: 19
Start: 'Mars'. End: 'Ludwig van Beethoven'. Page: 4
Start: 'Mars'. End: 'Mount Everest'. Page: 2
Start: 'Mars'. End: 'Humpback whale'. Page: 4
Start: 'Mars'. End: 'Great Wall of China'. Page: 13
Start: 'Mars'. End: 'Photography'. Page: 32
Start: 'Mars'. End: 'Egyptian pyramids'. Page: 3
Start: 'Mars'. End: 'Albert Einstein'. Page: 6
Start: 'Mars'. End: 'Rainforest'. Page: 7
Start: 'Mars'. End: 'Buggy'. Page: 200
Start: 'Beethoven'. End: 'Sushi'. Page: 17
Start: 'Beethoven'. End: 'Mars'. Page: 3

In [64]:
print(master_dict.keys())
print([len(master_dict[key]) for key in master_dict.keys()])

dict_keys(['start', 'target', 'topic', 'context', 'sim_to_target', 'url', 'page_num'])
[3238, 3238, 3238, 3238, 3238, 3238, 3238]


In [66]:
master_df = pd.DataFrame(master_dict)
master_df.to_csv("data/3238x7.csv", index = False)
master_df

start      target                         topic  \
0     Sushi        Mars                         Sushi   
1     Sushi        Mars                  Planet Money   
2     Sushi        Mars           Pacifica Foundation   
3     Sushi        Mars                     Mars Hill   
4     Sushi        Mars              Equinox Mountain   
...     ...         ...                           ...   
3233  buggy  Rainforest  Forests of the United States   
3234  buggy  Rainforest                boreal forests   
3235  buggy  Rainforest             Deciduous forests   
3236  buggy  Rainforest     Tropical deciduous forest   
3237  buggy  Rainforest                   rainforests   

                                                context  sim_to_target  \
0     Sushi (すし, 寿司, 鮨, 鮓, pronounced [sɯɕiꜜ] or [sɯ...       0.046150   
1     Planet Money is an American podcast and blog p...       0.494693   
2     Pacifica Foundation is an American non-profit ...       0.186643   
3     The Mars Hill Network is a network of Christia...       0.466525   
4     Equinox Mountain is the highest peak of the Ta...       0.196999   
...                                                 ...            ...   
3233  It has been estimated that before European set...       0.437653   
3234  Taiga (/ˈtaɪɡə/; Russian: тайга́; relates to M...       0.474700   
3235  Temperate deciduous or temperate broad-leaf fo...       0.501480   
3236  The tropical and subtropical dry broadleaf for...       0.480779   
3237  Rainforests are forests characterized by a clo...       0.482825   

                                                    url  page_num  
0                   https://en.wikipedia.org/wiki/Sushi         1  
1            https://en.wikipedia.org/wiki/Planet_Money         2  
2     https://en.wikipedia.org/wiki/Pacifica_Foundation         3  
3       https://en.wikipedia.org/wiki/Mars_Hill_Network         4  
4        https://en.wikipedia.org/wiki/Equinox_Mountain         5  
...                                                 ...       ...  
3233  https://en.wikipedia.org/wiki/Forests_of_the_U...         5  
3234        https://en.wikipedia.org/wiki/Boreal_forest         6  
3235  https://en.wikipedia.org/wiki/Temperate_decidu...         7  
3236  https://en.wikipedia.org/wiki/Tropical_deciduo...         8  
3237           https://en.wikipedia.org/wiki/Rainforest         9  

[3238 rows x 7 columns]